In [1]:
import mdtraj

from grand import lig_samplers as ls
from grand import lig_utils as lu

import openmm
import openmm.app
import openmm.unit
from pdbfixer import PDBFixer

import openff.toolkit

from openmmtools.integrators import VelocityVerletIntegrator
from openmmtools.integrators import BAOABIntegrator

import numpy as np
import mdtraj as md
from scipy.spatial import Voronoi
import os
from collections import defaultdict
import tqdm
import pickle

Warning on use of the timeseries module: If the inherent timescales of the system are long compared to those being analyzed, this statistical inefficiency may be an underestimate.  The estimate presumes the use of many statistically independent samples.  Tests should be performed to assess whether this condition is satisfied.   Be cautious in the interpretation of the data.

****** PyMBAR will use 64-bit JAX! *******
* JAX is currently set to 32-bit bitsize *
* which is its default.                  *
*                                        *
* PyMBAR requires 64-bit mode and WILL   *
* enable JAX's 64-bit mode when called.  *
*                                        *
* This MAY cause problems with other     *
* Uses of JAX in the same code.          *
******************************************



In [2]:
mol = openff.toolkit.Molecule.from_smiles("c1ccccc1O")
mol.generate_conformers(n_conformers=1000)
topology = mol.to_topology().to_openmm()
positions = mol.conformers[0].to_openmm()

In [3]:
fixer = PDBFixer(filename='1l56.pdb')
fixer.findMissingResidues()
fixer.findNonstandardResidues()
fixer.replaceNonstandardResidues()
fixer.removeHeterogens(False)
fixer.findMissingAtoms()
fixer.addMissingAtoms()
fixer.addMissingHydrogens(7.0)
openmm.app.PDBFile.writeFile(fixer.topology, fixer.positions, open('apo.pdb', 'w'))

In [4]:
prot = openmm.app.PDBFile('apo.pdb')

In [5]:
if os.path.exists('gcmc-ghosts-20.pdb'):
    pdb = openmm.app.PDBFile('gcmc-ghosts-20.pdb')
    sys_top = pdb.topology
    sys_pos = pdb.positions
else:
    sys_top, sys_pos, ghosts = lu.add_ghosts(prot.topology, prot.positions, topology, positions, n=20, output='gcmc-ghosts-20.pdb')

In [6]:
if os.path.exists('gcmc-ghosts-1000.pdb'):
    pdb = openmm.app.PDBFile('gcmc-ghosts-1000.pdb')
    sys_top = pdb.topology
    sys_pos = pdb.positions
else:
    sys_top, sys_pos, ghosts = lu.add_ghosts(prot.topology, prot.positions, topology, positions, n=1000,output='gcmc-ghosts-1000.pdb')

In [7]:
ff = openmm.app.ForceField('amber14-all.xml', 'amber14/tip3pfb.xml','phenol_openff.xml')

In [8]:
prot_system = ff.createSystem(prot.topology, nonbondedMethod=openmm.app.CutoffPeriodic)
integrator = openmm.LangevinIntegrator(
    298.0 * openmm.unit.kelvin, 1.0 / openmm.unit.picosecond, 2.0 * openmm.unit.femtosecond
)
#integrator = openmm.VerletIntegrator(
#    1.0 * openmm.unit.femtosecond
#)
#integrator = BAOABIntegrator(298*openmm.unit.kelvin, 1.0/openmm.unit.picosecond, 0.002*openmm.unit.picoseconds)
simulation = openmm.app.Simulation(prot.topology,prot_system,integrator)

In [9]:
pdb = openmm.app.PDBFile('gcmc-ghosts-1000.pdb')

In [10]:
pdb_system = ff.createSystem(pdb.topology)
integrator = openmm.LangevinIntegrator(
    298.0 * openmm.unit.kelvin, 1.0 / openmm.unit.picosecond, 2.0 * openmm.unit.femtosecond
)

In [11]:
pdb_system.getDefaultPeriodicBoxVectors()

[Quantity(value=Vec3(x=6.11, y=0.0, z=0.0), unit=nanometer),
 Quantity(value=Vec3(x=-3.054999999999999, y=5.291415217122921, z=0.0), unit=nanometer),
 Quantity(value=Vec3(x=0.0, y=0.0, z=9.64), unit=nanometer)]

In [12]:
frag_res_ids = []
for resid, residue in enumerate(pdb.topology.residues()):
    if residue.name == "UNK":
        frag_res_ids.append(resid)

In [13]:
sampler = ls.BaseGCMCSampler(pdb_system,pdb.topology,298*openmm.unit.kelvin,frag_res_ids,overwrite=True)

0.49048223350253806 /(nm**3) 1.4904822335025378 /nm 138.93545764438198
n_exception 69357
55000
1 5
<openmm.openmm.NonbondedForce; proxy of <Swig Object of type 'OpenMM::NonbondedForce *' at 0x736853415560> >


In [14]:
reporter = openmm.app.DCDReporter("phenol_sacp_quench1.dcd", reportInterval=1000)
state_reporter = openmm.app.StateDataReporter("energy.csv",reportInterval=100,potentialEnergy=True,kineticEnergy=True,density=True)

In [15]:
sampler.initialize(5, 1.0, pdb.positions,integrator,reporter)

HarmonicBondForce
1
37047.85617733002 kJ/mol
PeriodicTorsionForce
2
14468.93486344954 kJ/mol
CMMotionRemover
3
0.0 kJ/mol
HarmonicAngleForce
4
81764.18884277344 kJ/mol
CustomNonbondedForce
5
-28283.10752746463 kJ/mol
CustomBondForce
6
28608.688301086426 kJ/mol
Initial Energy: 133606.5598192215 kJ/mol


In [16]:
sampler.simulation.reporters.append(reporter)


In [17]:
f = open('real_res_ids.txt','w')
for n in tqdm.tqdm(range(50)):
    sampler.move()
    #sampler.reporter.report(sampler.simulation,sampler.context.getState(getPositions=True,getEnergy=True))
    f.write(','.join(sampler.real_lig_res_ids)+'\n')
print(sampler.n_accepted)

 46%|████▌     | 23/50 [01:38<02:30,  5.59s/it]

Explosion


 60%|██████    | 30/50 [02:05<01:17,  3.89s/it]

Explosion


100%|██████████| 50/50 [03:35<00:00,  4.31s/it]

15


In [18]:
sampler.simulation.saveCheckpoint('insert.ckpt')
sampler.simulation.saveState('insert.xml')
with open('real_lig_ckpt.pkl','wb') as f:
    pickle.dump(sampler.real_lig_res_ids,f)

In [19]:
sampler.simulation.loadCheckpoint('insert.ckpt')
sampler.simulation.loadState('insert.xml')

In [20]:
len(sampler.ghost_lig_res_ids)

985

In [21]:
openmm.app.PDBFile.writeFile(sampler.topology, sampler.positions,open('insert.pdb','w'))

In [22]:
modeller = openmm.app.Modeller(sampler.topology, sampler.positions)
toDelete = [r for r in sampler.topology.residues() if r.index in sampler.ghost_lig_res_ids]
modeller.delete(toDelete)

In [23]:
modeller.topology.getPeriodicBoxVectors()

Quantity(value=(Vec3(x=6.11, y=0.0, z=0.0), Vec3(x=-3.054999999999999, y=5.291415217122921, z=0.0), Vec3(x=0.0, y=0.0, z=9.64)), unit=nanometer)

In [24]:
modeller.addSolvent(forcefield=ff,padding=1*openmm.unit.nanometer)

In [25]:
openmm.app.PDBFile.writeFile(modeller.topology, modeller.positions,open('solvated.pdb','w'))

In [26]:
pdb = openmm.app.PDBFile('solvated.pdb')

In [27]:
ff = openmm.app.ForceField('amber14-all.xml', 'amber14/tip3pfb.xml','phenol_openff.xml')

In [28]:
sol_system = ff.createSystem(pdb.topology)
integrator = openmm.LangevinIntegrator(
    298.0 * openmm.unit.kelvin, 1.0 / openmm.unit.picosecond, 2.0 * openmm.unit.femtosecond
)

In [29]:
lig_list = []
for resid, residue in enumerate(pdb.topology.residues()):
    if residue.name == 'UNK':
        lig_list.append(resid)

In [30]:
new_sampler = ls.BaseGCMCSampler(sol_system,pdb.topology,298*openmm.unit.kelvin,lig_list,overwrite=True)

0.49048223350253806 /(nm**3) 1.4904822335025378 /nm 138.93545764438198
n_exception 46124
2830 2831 0.0 e**2 1.0 nm 0.0 kJ/mol
2830 2832 0.0 e**2 1.0 nm 0.0 kJ/mol
2831 2832 0.0 e**2 1.0 nm 0.0 kJ/mol
2833 2834 0.0 e**2 1.0 nm 0.0 kJ/mol
2833 2835 0.0 e**2 1.0 nm 0.0 kJ/mol
2834 2835 0.0 e**2 1.0 nm 0.0 kJ/mol
2836 2837 0.0 e**2 1.0 nm 0.0 kJ/mol
2836 2838 0.0 e**2 1.0 nm 0.0 kJ/mol
2837 2838 0.0 e**2 1.0 nm 0.0 kJ/mol
2839 2840 0.0 e**2 1.0 nm 0.0 kJ/mol
2839 2841 0.0 e**2 1.0 nm 0.0 kJ/mol
2840 2841 0.0 e**2 1.0 nm 0.0 kJ/mol
2842 2843 0.0 e**2 1.0 nm 0.0 kJ/mol
2842 2844 0.0 e**2 1.0 nm 0.0 kJ/mol
2843 2844 0.0 e**2 1.0 nm 0.0 kJ/mol
2845 2846 0.0 e**2 1.0 nm 0.0 kJ/mol
2845 2847 0.0 e**2 1.0 nm 0.0 kJ/mol
2846 2847 0.0 e**2 1.0 nm 0.0 kJ/mol
2848 2849 0.0 e**2 1.0 nm 0.0 kJ/mol
2848 2850 0.0 e**2 1.0 nm 0.0 kJ/mol
2849 2850 0.0 e**2 1.0 nm 0.0 kJ/mol
2851 2852 0.0 e**2 1.0 nm 0.0 kJ/mol
2851 2853 0.0 e**2 1.0 nm 0.0 kJ/mol
2852 2853 0.0 e**2 1.0 nm 0.0 kJ/mol
2854 2855 0.0 e**2 1.0 

In [31]:
reporter = openmm.app.DCDReporter("phenol_solvated.dcd", reportInterval=1000)

In [32]:
new_sampler.initialize(100, 1.0, pdb.positions,integrator,reporter)

HarmonicBondForce
1
36370.73645019531 kJ/mol
PeriodicTorsionForce
2
14468.46068572998 kJ/mol
CMMotionRemover
3
0.0 kJ/mol
HarmonicAngleForce
4
18542.241333007812 kJ/mol
CustomNonbondedForce
5
12466946177.812012 kJ/mol
CustomBondForce
6
28608.688301086426 kJ/mol
Initial Energy: 12467044159.76773 kJ/mol


In [33]:
sampler.lig_atom_ids

defaultdict(list,
            {164: [2635,
              2636,
              2637,
              2638,
              2639,
              2640,
              2641,
              2642,
              2643,
              2644,
              2645,
              2646,
              2647],
             165: [2648,
              2649,
              2650,
              2651,
              2652,
              2653,
              2654,
              2655,
              2656,
              2657,
              2658,
              2659,
              2660],
             166: [2661,
              2662,
              2663,
              2664,
              2665,
              2666,
              2667,
              2668,
              2669,
              2670,
              2671,
              2672,
              2673],
             167: [2674,
              2675,
              2676,
              2677,
              2678,
              2679,
              2680,
              2681,
              2682,

In [34]:
for atom_idx in range(new_sampler.nonbonded_force.getNumParticles()):
    # Get atom parameters
    print(new_sampler.nonbonded_force.getParticleParameters(atom_idx))

(0.0, 0.1592, 0.3249998523775958, 0.7112800000000001, 1.0)
(0.0, 0.1984, 0.10690784617684071, 0.06568879999999999, 1.0)
(0.0, 0.1984, 0.10690784617684071, 0.06568879999999999, 1.0)
(0.0, 0.1984, 0.10690784617684071, 0.06568879999999999, 1.0)
(0.0, 0.0221, 0.3399669508423535, 0.4577296, 1.0)
(0.0, 0.1116, 0.19599771799087468, 0.06568879999999999, 1.0)
(0.0, 0.6123, 0.3399669508423535, 0.359824, 1.0)
(0.0, -0.5713, 0.2959921901149463, 0.87864, 1.0)
(0.0, 0.0865, 0.3399669508423535, 0.4577296, 1.0)
(0.0, 0.0125, 0.2649532787749369, 0.06568879999999999, 1.0)
(0.0, 0.0125, 0.2649532787749369, 0.06568879999999999, 1.0)
(0.0, 0.0334, 0.3399669508423535, 0.4577296, 1.0)
(0.0, 0.0292, 0.2471353044121301, 0.06568879999999999, 1.0)
(0.0, 0.0292, 0.2471353044121301, 0.06568879999999999, 1.0)
(0.0, -0.2774, 0.35635948725613575, 1.046, 1.0)
(0.0, -0.0341, 0.3399669508423535, 0.4577296, 1.0)
(0.0, 0.0597, 0.2471353044121301, 0.06568879999999999, 1.0)
(0.0, 0.0597, 0.2471353044121301, 0.06568879999999

In [35]:
new_sampler.lig_atom_ids

defaultdict(list,
            {164: [2635,
              2636,
              2637,
              2638,
              2639,
              2640,
              2641,
              2642,
              2643,
              2644,
              2645,
              2646,
              2647],
             165: [2648,
              2649,
              2650,
              2651,
              2652,
              2653,
              2654,
              2655,
              2656,
              2657,
              2658,
              2659,
              2660],
             166: [2661,
              2662,
              2663,
              2664,
              2665,
              2666,
              2667,
              2668,
              2669,
              2670,
              2671,
              2672,
              2673],
             167: [2674,
              2675,
              2676,
              2677,
              2678,
              2679,
              2680,
              2681,
              2682,

In [36]:
atoms = []
for res_id in new_sampler.lig_res_ids:
    for atom_id in new_sampler.lig_atom_ids[res_id]:
        atoms.append(atom_id)
new_sampler.adjust_specific_ligand(atoms,new_sampler.lig_params,'on')

In [37]:
new_sampler.nonbonded_force.getParticleParameters(atom_id)

(1.0, 0.4180200088482637, 0.053453923088366904, 5.157198260534728e-05, 1.0)

In [38]:
new_sampler.system.setDefaultPeriodicBoxVectors(*pdb.topology.getPeriodicBoxVectors())

In [39]:
new_sampler.simulation.minimizeEnergy()

OpenMMException: Particle coordinate is NaN.  For more information, see https://github.com/openmm/openmm/wiki/Frequently-Asked-Questions#nan

In [ ]:
new_sampler.system.getDefaultPeriodicBoxVectors()

[Quantity(value=Vec3(x=7.1039, y=0.0, z=0.0), unit=nanometer),
 Quantity(value=Vec3(x=0.0, y=7.1039, z=0.0), unit=nanometer),
 Quantity(value=Vec3(x=0.0, y=0.0, z=7.1039), unit=nanometer)]

In [ ]:
new_sampler.positions.min()

Quantity(value=Vec3(x=-0.2602, y=-1.5256, z=-1.7843), unit=nanometer)

In [ ]:
openmm.app.PDBFile.writeFile(new_sampler.topology,new_sampler.positions,'test_solvated.pdb')

In [ ]:
new_reporter = openmm.app.DCDReporter("solvated_test.dcd", reportInterval=1000)

In [ ]:
new_sampler.simulation.reporters.append(new_reporter)

In [ ]:
new_sampler.system.addForce(openmm.MonteCarloBarostat(1*openmm.unit.bar, 298*openmm.unit.kelvin))
new_sampler.simulation.context.reinitialize(preserveState=True)

In [ ]:
new_sampler.simulation.step(100000)

OpenMMException: Particle coordinate is NaN.  For more information, see https://github.com/openmm/openmm/wiki/Frequently-Asked-Questions#nan

In [ ]:
sampler.B = -10 #* openmm.unit.kilojoules_per_mole
sampler.insert_prob = 0.1

In [ ]:
openmm.app.PDBFile.writeFile(new_sampler.topology,new_sampler.context.getState(getPositions=True).getPositions(),'test_solvated2.pdb')

In [ ]:
new_sampler.context.getState(getPositions=True).getPositions()

Quantity(value=[Vec3(x=4.935242652893066, y=-0.4513545632362366, z=0.7128301858901978), Vec3(x=4.977739334106445, y=-0.4597853422164917, z=0.8074988722801208), Vec3(x=4.880982398986816, y=-0.532734751701355, z=0.6912786364555359), Vec3(x=5.012946605682373, y=-0.4407612979412079, z=0.6452047228813171), Vec3(x=4.83800745010376, y=-0.33691641688346863, z=0.7078412175178528), Vec3(x=4.877054691314697, y=-0.25778651237487793, z=0.7720749378204346), Vec3(x=4.699007511138916, y=-0.37999966740608215, z=0.7575222849845886), Vec3(x=4.616354942321777, y=-0.4367028474807739, z=0.6828901171684265), Vec3(x=4.8222737312316895, y=-0.26840269565582275, z=0.5706951022148132), Vec3(x=4.795379638671875, y=-0.3458247780799866, z=0.5119797587394714), Vec3(x=4.919523239135742, y=-0.22853495180606842, z=0.5427770614624023), Vec3(x=4.71551513671875, y=-0.15244688093662262, z=0.5735695958137512), Vec3(x=4.768099784851074, y=-0.07133129239082336, z=0.6204513311386108), Vec3(x=4.630929470062256, y=-0.175662904977

In [ ]:
f = open('real_res_ids.txt','w')
for n in tqdm.tqdm(range(100)):
    sampler.move()
    #sampler.reporter.report(sampler.simulation,sampler.context.getState(getPositions=True,getEnergy=True))
    f.write(','.join(sampler.real_lig_res_ids)+'\n')
print(sampler.n_accepted)

  1%|          | 1/100 [00:10<17:20, 10.51s/it]

kept:  627 -118.79245484757013
kept:  880 -126.17917709254955


  5%|▌         | 5/100 [00:31<06:35,  4.17s/it]

deleted:  1044 -0.0
deleted:  627 -0.0


  7%|▋         | 7/100 [00:54<12:24,  8.01s/it]

kept:  880 -1961.9534333919737


  8%|▊         | 8/100 [01:04<12:25,  8.10s/it]

deleted:  880 59.02562883451727


ValueError: 'a' cannot be empty unless no samples are taken

In [ ]:
sampler.ghost_lig_res_ids[-48:]

[1151,
 1152,
 1153,
 1154,
 1155,
 1156,
 1157,
 1159,
 1160,
 1161,
 1162,
 1163,
 '294',
 '408',
 '685',
 '1158',
 '377',
 '187',
 '650',
 '478',
 '207',
 '252',
 '528',
 '455',
 '522',
 '777',
 '353',
 '1131',
 '394',
 '381',
 '333',
 '183',
 '665',
 '749',
 '628',
 '965',
 '457',
 '868',
 '391',
 '483',
 '884',
 '932',
 '742',
 '744',
 '829',
 '824',
 '438',
 '297']